Download a parquet file to your Google drive and load it from there into this notebook.

Parquet files: https://huggingface.co/datasets/codeShare/chroma_prompts/tree/main

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Step 1: Mount Google Drive
#from google.colab import drive
#drive.mount('/content/drive')

#@markdown paste .parquet file stored on your Google Drive folder to see its characteristics

# Step 2: Import required libraries
import pandas as pd

# Step 3: Define the path to the Parquet file
file_path = '/content/drive/MyDrive/Chroma prompts/redcaps_1.parquet' #@param {type:'string'}

# Step 4: Read the Parquet file
df = pd.read_parquet(file_path)

# Step 5: Basic exploration of the Parquet file
print("First 5 rows of the dataset:")
print(df.head())

print("\nDataset Info:")
print(df.info())

print("\nBasic Statistics:")
print(df.describe())

print("\nColumn Names:")
print(df.columns.tolist())

print("\nMissing Values:")
print(df.isnull().sum())

# Optional: Display number of rows and columns
print(f"\nShape of the dataset: {df.shape}")

In [ ]:

#@markdown Build a dataset for training using a .parquet file

num_dataset_items = 200 #@param {type:'slider',max:1000}



# Step 1: Install required libraries (if not already installed)
# !pip install datasets pandas pillow requests

# Step 2: Import required libraries
import pandas as pd
from datasets import Dataset
from PIL import Image
import requests
from io import BytesIO
import numpy as np

# Step 3: Define the path to the Parquet file
file_path = '/content/drive/MyDrive/Chroma prompts/redcaps_1.parquet' #@param {type:'string'}

# Step 4: Read the Parquet file
df = pd.read_parquet(file_path)

# Step 5: Randomly select 300 rows to account for potential image loading failures
df_sample = df.sample(n=math.floor(num_dataset_items*1.2), random_state=42).reset_index(drop=True)

# Step 6: Function to download, resize, and process images
def load_and_resize_image_from_url(url, max_size=(1024, 1024)):
    try:
        response = requests.get(url, timeout=10)
        response.raise_for_status()  # Raise an error for bad status codes
        img = Image.open(BytesIO(response.content)).convert('RGB')
        # Resize image to fit within 1024x1024 while maintaining aspect ratio
        img.thumbnail(max_size, Image.Resampling.LANCZOS)
        return img
    except Exception as e:
        print(f"Error loading image from {url}: {e}")
        return None

# Step 7: Create lists for images and captions
images = []
texts = []

for index, row in df_sample.iterrows():
    if len(images) >= num_dataset_items:  # Stop once we have 200 valid images
        break
    url = row['url']
    caption = row['original_caption'] + ', ' + row['vlm_caption'].replace('This image displays:','').replace('This image displays','')

    # Load and resize image
    img = load_and_resize_image_from_url(url)
    if img is not None:
        images.append(img)
        texts.append(caption)
    else:
        print(f"Skipping row {index} due to image loading failure.")

# Step 8: Check if we have enough images
if len(images) < num_dataset_items:
    print(f"Warning: Only {len(images)} images were successfully loaded.")
else:
    # Truncate to exactly 200 if we have more
    images = images[:num_dataset_items]
    texts = texts[:num_dataset_items]

# Step 9: Create a Hugging Face Dataset
dataset = Dataset.from_dict({
    'image': images,
    'text': texts
})

# Step 10: Verify the dataset
print(dataset)

# Step 11: Example of accessing an image and text
print("\nExample of accessing first item:")
print("Text:", dataset['text'][0])
print("Image type:", type(dataset['image'][0]))
print("Image size:", dataset['image'][0].size)

# Optional: Save the dataset to disk (if needed)
dataset.save_to_disk('/content/drive/MyDrive/Chroma prompts/custom_dataset')

In [ ]:
dataset.save_to_disk('/content/drive/MyDrive/redcap_dataset')

In [ ]:
dataset['image'][10]

In [ ]:
# Import pandas
import pandas as pd

# Define the path to the Parquet file
file_path = '/content/drive/MyDrive/Chroma prompts/e621_2024_p10.parquet' #@param {type:'string'}

parquet_column = 'descriptions' #@param {type:'string'}
# Read the Parquet file
df = pd.read_parquet(file_path)

# Set pandas display options to show full text without truncation
pd.set_option('display.max_colwidth', None)  # Show full content of columns
pd.set_option('display.width', None)         # Use full display width

# Create sliders for selecting the range of captions
#@markdown Caption Range { run: "auto", display_mode: "form" }
start_at = 16814 #@param {type:"slider", min:0, max:33147, step:1}
range = 247 #@param {type:'slider',min:1,max:1000,step:1}
start_index = start_at
end_index = start_at + range
###@param {type:"slider", min:1, max:33148, step:1}

include_either_words = '' #@param {type:'string', placeholder:'item1,item2...'}
#display_only = True #@param {type:'boolean'}

_include_either_words = ''
for include_word in include_either_words.split(','):
  if include_word.strip()=='':continue
  _include_either_words= include_either_words + include_word.lower()+','+include_word.title() +','
#-----#
_include_either_words = _include_either_words[:len(_include_either_words)-1]


# Ensure end_index is greater than start_index and within bounds
if end_index <= start_index:
    print("Error: End index must be greater than start index.")
elif end_index > len(df):
    print(f"Error: End index cannot exceed {len(df)}. Setting to maximum value.")
    end_index = len(df)
elif start_index < 0:
    print("Error: Start index cannot be negative. Setting to 0.")
    start_index = 0

# Display the selected range of captions
tmp =''

categories= ['regular_summary:',';midjourney_style_summary:', 'individual_parts:']

print(f"\nDisplaying captions from index {start_index} to {end_index-1}:")
for index, caption in df[f'{parquet_column}'][start_index:end_index].items():
  for include_word in _include_either_words.split(','):
    found = True
    if (include_word.strip() in caption) or include_word.strip()=='':
      #----#
      if not found: continue
      tmp= caption + '\n\n'
      for category in categories:
        tmp = tmp.replace(f'{category}',f'\n\n{category}\n')
      #----#
      print(f'Index {index}: {tmp}')
